In [1]:
from keras.models import Sequential

from keras.layers import Dense, Dropout, Flatten

from keras.layers import Conv2D, MaxPooling2D

from keras.preprocessing import image

import numpy as np

import pandas as pd

from tqdm import tqdm

from keras.applications.vgg16 import VGG16

import cv2

import math

import os

from glob import glob

from scipy import stats as s

In [11]:
pip show tensorflow

Name: tensorflow
Version: 2.16.1
Summary: TensorFlow is an open source machine learning framework for everyone.
Home-page: https://www.tensorflow.org/
Author: Google Inc.
Author-email: packages@tensorflow.org
License: Apache 2.0
Location: c:\users\bruce\appdata\local\programs\python\python310\lib\site-packages
Requires: tensorflow-intel
Required-by: 
Note: you may need to restart the kernel to use updated packages.


In [2]:
base_model = VGG16(weights='imagenet', include_top=False)

In [3]:
#defining the classifier model architecture

model = Sequential()

model.add(Dense(1024, activation='relu', input_shape=(2048,)))

model.add(Dropout(0.5))

model.add(Dense(512, activation='relu'))

model.add(Dropout(0.5))

model.add(Dense(256, activation='relu'))

model.add(Dropout(0.5))

model.add(Dense(128, activation='relu'))

model.add(Dropout(0.5))

model.add(Dense(101, activation='softmax'))

C:\Users\Bruce\AppData\Local\Programs\Python\Python310\lib\site-packages\keras\src\layers\core\dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


In [4]:
# loading the trained weights

model.load_weights("weight.keras")

#Compile the model as well:

# compiling the model

model.compile(loss='categorical_crossentropy',optimizer='Adam',metrics=['accuracy'])

In [5]:
f = open("testlist01.txt", "r")

temp = f.read()

videos = temp.split('\n')



# creating the dataframe
test = pd.DataFrame()
test['video_name'] = videos
test = test[:-1]
test_videos = test['video_name']
test.head()

video_name
0  ApplyEyeMakeup
1   ApplyLipstick
2         Archery
3    BabyCrawling
4     BalanceBeam

In [6]:
# creating the tags
train = pd.read_csv('train_new.csv')
y = train['class']
y = pd.get_dummies(y)

In [7]:
print(test_videos.tolist())

['ApplyEyeMakeup', 'ApplyLipstick', 'Archery', 'BabyCrawling', 'BalanceBeam', 'BandMarching', 'BaseballPitch', 'Basketball', 'BasketballDunk', 'BenchPress', 'Biking', 'Billiards', 'BlowDryHair', 'BlowingCandles', 'BodyWeightSquats', 'Bowling', 'BoxingPunchingBag', 'BoxingSpeedBag', 'BreastStroke', 'BrushingTeeth', 'CleanAndJerk', 'CliffDiving', 'CricketBowling', 'CricketShot', 'CuttingInKitchen', 'Diving', 'Drumming', 'Fencing', 'FieldHockeyPenalty', 'FloorGymnastics', 'FrisbeeCatch', 'FrontCrawl', 'GolfSwing', 'Haircut', 'Hammering', 'HammerThrow', 'HandstandPushups', 'HandstandWalking', 'HeadMassage', 'HighJump', 'HorseRace', 'HorseRiding', 'HulaHoop', 'IceDancing', 'JavelinThrow', 'JugglingBalls', 'JumpingJack', 'JumpRope', 'Kayaking', 'Knitting', 'LongJump', 'Lunges', 'MilitaryParade', 'Mixing', 'MoppingFloor', 'Nunchucks', 'ParallelBars', 'PizzaTossing', 'PlayingCello', 'PlayingDaf', 'PlayingDhol', 'PlayingFlute', 'PlayingGuitar', 'PlayingPiano', 'PlayingSitar', 'PlayingTabla', 'P

In [29]:
# creating two lists to store predicted and actual tags
predict = []
actual = [] 

# defining a function to extract features from test videos
def extract_features(test_videos):
    for i in tqdm(range(test_videos.shape[0])): 
        count = 0 
        videoFile = test_videos[i]
        folder_path = 'Videos/UCF-101/'+videoFile.split(' ')[0].split('/')[0]
        video_files = [f for f in os.listdir(folder_path) if f.endswith('.avi')]

        for video_file in video_files:
            video_path = os.path.join(folder_path, video_file)  # Full path to the video file
            cap = cv2.VideoCapture(video_path)
            frameRate = cap.get(5) # frame rate 
            x=1
            files = glob('temp/*') 
            # removing all other files from the temp folder
            for f in files: 
                os.remove(f) 

            while(cap.isOpened()): 
                frameId = cap.get(1) # current frame number
                ret, frame = cap.read() 
                if (ret != True): 
                    break 
                if (frameId % math.floor(frameRate) == 0): 
                    # storing the frames of this particular video in temp folder
                    filename ='temp/' + "_frame%d.jpg" % count;count+=1 
                    cv2.imwrite(filename, frame) 

            cap.release() 

            images = glob("temp/*.jpg")
            prediction_images = []
    
            for img_path in images:
                img = image.load_img(img_path, target_size=(64, 64))
                img = image.img_to_array(img)
                img = img/255
                prediction_images.append(img)
    
            prediction_images = np.array(prediction_images)
            prediction_images = base_model.predict(prediction_images)
            prediction_images = prediction_images.reshape(prediction_images.shape[0], 2*2*512)
    
            #prediction = model.predict_classes(prediction_images)
            prediction = np.argmax(model.predict(prediction_images), axis=-1)
            predict.append(prediction[0])
            actual.append(videoFile.split('.')[0])

    return predict, actual

# Extract features from test videos
predictions, actual_tags = extract_features(test_videos)

# Print predicted and actual tags
print("Predicted Tags:", predictions)
print("Actual Tags:", actual_tags)

# Count occurrences of each tag
tag_counts = Counter(predictions)
print("Tag Counts:", tag_counts)


  0%|                                                                                          | 0/101 [00:00<?, ?it/s]

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 232ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 135ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 439ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 123ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 475ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 419ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 535ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 219ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 266ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 234ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 35ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 339ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 297ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 361ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 250ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 236ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/st

  1%|▊                                                                              | 1/101 [01:42<2:51:04, 102.65s/it]

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 256ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 297ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 484ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 589ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 63ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 344ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 250ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 222ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 156ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 266ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 281ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 234ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 250ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 266ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step

  2%|█▌                                                                              | 2/101 [03:02<2:26:47, 88.97s/it]

...

 99%|████████████████████████████████████████████████████████████████████████████▏| 100/101 [2:57:20<01:44, 104.05s/it]

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 376ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 350ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 344ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 359ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 380ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 27ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 342ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 55ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 359ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 33ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 344ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 392ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 35ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 340ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 33ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 328ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 297ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 331ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step

100%|█████████████████████████████████████████████████████████████████████████████| 101/101 [2:58:57<00:00, 106.32s/it]

Predicted Tags: [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 9, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2,

NameError: name 'Counter' is not defined

In [34]:
from collections import Counter
# Count occurrences of each tag
tag_counts = Counter(predictions)
print("Tag Counts:", tag_counts)

Tag Counts: Counter({95: 181, 91: 175, 77: 170, 70: 170, 60: 167, 26: 167, 41: 167, 64: 165, 62: 165, 58: 164, 9: 163, 46: 163, 16: 162, 43: 162, 6: 161, 99: 160, 22: 159, 5: 158, 61: 156, 48: 154, 75: 154, 25: 154, 73: 152, 59: 151, 12: 150, 11: 150, 15: 150, 84: 150, 83: 150, 67: 147, 23: 147, 38: 147, 0: 146, 2: 145, 35: 143, 86: 143, 31: 143, 80: 143, 34: 143, 89: 141, 32: 140, 17: 138, 19: 137, 53: 136, 94: 136, 55: 135, 7: 134, 40: 134, 8: 133, 88: 133, 98: 133, 10: 132, 50: 132, 51: 129, 36: 129, 76: 129, 68: 128, 28: 128, 87: 127, 29: 127, 45: 126, 100: 126, 85: 125, 92: 124, 49: 124, 47: 123, 3: 122, 42: 122, 33: 121, 52: 121, 93: 119, 1: 117, 27: 116, 24: 115, 96: 115, 82: 115, 44: 114, 74: 114, 97: 112, 20: 112, 65: 111, 81: 109, 72: 108, 54: 108, 63: 108, 13: 107, 79: 106, 18: 106, 14: 105, 37: 105, 56: 103, 30: 103, 21: 102, 69: 101, 66: 101, 90: 100, 71: 93, 57: 89, 39: 72, 78: 72, 4: 40})


In [37]:
print(actual)


['ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEyeMakeup', 'ApplyEye

In [8]:
test_videos.head

<bound method NDFrame.head of 0         ApplyEyeMakeup
1          ApplyLipstick
2                Archery
3           BabyCrawling
4            BalanceBeam
             ...        
96     VolleyballSpiking
97        WalkingWithDog
98           WallPushups
99        WritingOnBoard
100                 YoYo
Name: video_name, Length: 101, dtype: object>

In [8]:
import os

# Directory containing test images
testing_dir = "testing"

# List all files in the test directory
testing_files = os.listdir(testing_dir)

# Filter only JPEG files
testing_images = [os.path.join(testing_dir, file) for file in testing_files if file.endswith(".jpg")]

# Example test videos list
testing_videos = testing_images[:5]  # Assuming you want to use the first 5 images for testing

print("Test Videos:", testing_videos)


Test Videos: ['testing\\download.jpg', 'testing\\_frame988.jpg', 'testing\\_frame989.jpg', 'testing\\_frame990.jpg', 'testing\\_frame991.jpg']


In [9]:
class_names = test_videos.tolist()
def extract_features(test_videos):
            
        images = glob("testing/*.jpg")
        prediction_images = []
    
        for img_path in images:
            img = image.load_img(img_path, target_size=(64, 64))
            img = image.img_to_array(img)
            img = img/255
            prediction_images.append(img)
    
        prediction_images = np.array(prediction_images)
        prediction_images = base_model.predict(prediction_images)
        prediction_images = prediction_images.reshape(prediction_images.shape[0], 2*2*512)
    
        #prediction = model.predict_classes(prediction_images)
        #prediction = np.argmax(model.predict(prediction_images), axis=-1)
        #print(
        prediction_indices = np.argmax(model.predict(prediction_images), axis=-1)
        predictions = [class_names[idx] for idx in prediction_indices]
        #print(prediction)
        #predict.append(prediction[0])
        #actual.append(videoFile.split('.')[0])

        return predictions#, actual

# Extract features from test videos
#testing_videos = []
predictions = extract_features(testing_videos)
# Print predicted and actual tags
print("Predicted Tags:", predictions)
#print("Actual Tags:", actual_tags)



1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 481ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 98ms/step
Predicted Tags: ['ApplyLipstick', 'YoYo', 'YoYo', 'YoYo', 'YoYo', 'YoYo', 'YoYo', 'YoYo', 'YoYo']


In [10]:
import cv2

def extract_features(video_path):
    # Open the video file
    #print("Video Path:", video_path)  # Debugging line
    cap = cv2.VideoCapture(0)
    predictions = []

    # Check if the video opened successfully
    if not cap.isOpened():
        print("Error opening video file")
        return predictions

    while True:
        ret, frame = cap.read()

        # If frame read successfully
        if ret:
            # Preprocess frame for object detection (resize, normalize, etc.)
            resized_frame = cv2.resize(frame, (64, 64))  # Resize to match model input size
            resized_frame = resized_frame / 255.0  # Normalize pixel values

            # Perform object detection using extract_features function
            prediction = extract_features([resized_frame])[0]  # Assuming extract_features takes a list of images

            # Append prediction to list
            predictions.append(prediction)

            # Display the frame with prediction (for visualization purposes)
            cv2.putText(frame, prediction, (10, 30), cv2.FONT_HERSHEY_SIMPLEX, 1, (0, 255, 0), 2)
            cv2.imshow('Frame', frame)

            # Press 'q' to exit video playback
            if cv2.waitKey(1) & 0xFF == ord('q'):
                break
        else:
            break

    # Release video capture and close OpenCV windows
    cap.release()
    cv2.destroyAllWindows()

    return predictions

# Example usage: Provide the path to your video file
video_path = 'E:\\Projects\\AI\\videoclassificationmodel\\Videos\\UCF-101\\ApplyEyeMakeup\\v_ApplyEyeMakeup_g01_c01.avi'
predictions = extract_features(video_path)
print("Predicted Tags for Video Frames:", predictions)



KeyboardInterrupt

